(yfinance)=
# Kursdaten: Import und Visualisierung

In diesem Kapitel beschäftigen wir uns damit, wie wir Kursdaten in Python verwenden können. Dabei sollen folgende Lerninhalte vermittelt werden: 

1. Einbettung und Anzeigen von Kursdaten
2. Visualisierung und Analyse von Kursen unter Einbeziehung von Charttechnik


## Einbettung und Anzeigen von Kursdaten

Grundsätzlich gibt es zwei Möglichkeiten Kurse in ein Python-Skript zu implementieren:

            a) Kursdaten werden in einer seperaten Datei aufbereitet (z.B. in .csv oder .xlsx Format)
            b) Direkter Abruf von Kursdaten aus dem Internet

Beginnen wir mit Variante a). Vorteilhaft ist es stets, die Datei der Kursdaten im gleichen Ordner zu haben. In diesem Fall verwenden wir das `pandas`-Package.

**Hinweise:** 
* Wenn es sich um eine *.xlsx-Datei* handelt muss im Vorfeld in die Python-Umgebung `openpyxl` installiert werden; handelt es sich um eine *.csv-Datei* reicht die Installation von `pandas` in der Python-Umgebung zu.
* Datenimport mittels relativer Pfade siehe  Pandas-Abschnitt {numref}`pandas-read` [](pandas-read)
<!-- https://jupyterbook.org/en/stable/content/references.html -->

Dies dann wie folgt aus: 
<a href="./Data/Allianz_Schlusskurse_2020_2025.csv" download>
  <button>📥 CSV herunterladen</button>
</a>
<!-- Make (funktioniert unter Linux aber nicht unter Windows) kopiert Data ordner nach _build/html/  -- check -->

In [ ]:
import pandas as pd

#df1 = pd.read_csv("./../../Data/Allianz_Schlusskurse_2020_2025.csv")
df1 = pd.read_csv("./../../Data/Allianz_Schlusskurse_2020_2025.csv", 
                       skiprows = 3, names = ["Datum", "Schlusskurs"])
#Achtung: bitte passen Sie den relativen Pfad an Ihre eigene Ordner-Struktur an


# Falls Sie eine xlsx-Datei einlesen wollen, die im gleichen Ordner liegt, dann würde der Code wiefolgt aussehen
# df = pd.read_excel("Datei.xlsx")

print(df1)

### Abruf von Kursdaten direkt aus Internet

Kommen wir nun zu unserer Variante b) und rufen Kursdaten direkt aus dem Internet ab. Dazu verwenden wir das Package `yfinance`.

**Hinweise:** 
* Das Ticker-Symbol einer Aktie finden wir auf der [Yahoo Finance-Webseite](https://finance.yahoo.com/quote/ALV.DE) hinter dem jeweiligen Aktientitel.
* Ab und zu hat Yahoo-Finance technische Probleme und der Kursabruf wie im direkt folgendem Beispiel funktioniert trotz fehlerfreien Codes nicht! Aus diesem Grund fangen wir im weiteren Beispiel dieses Problem ab, um unnötige Programmabbrüche zu vermeiden.
* Manchmal gibt es leider Probleme mit den aktuell installierten Paketen, so dass offensichtlich richtiger Code (hier beispielsweise zum Abrufen von Kursdaten mittels `yfinance` -- in einigen Fällen hilft ein Update des Paketes und manchmal eine De- und Neuinstallation. Falls die Download-Probleme also trotz richtigen Code anhalten, ist ein Wechsel auf eine stabile Version oder auch neuere Version möglich. Hierzu in der aktuellen Environment (myenv) erstmals die installierte Version überprüfen

        pip show yfinance

    und mittels pip auf die gewünsche Version zurücksetzen oder aktuallisieren (eine kurze Internetrecherche in diversen Foren ist hier sicherlich hilfreich), beispielsweise

        pip install yfinance==0.2.63
* Manchmal gibt es beim Download der Daten über YahooFinance oder andere (kostenlose) Quellen leider Probleme und sobald der Code deshalb Fehler verursacht, stoppt ein Script. Will man dies vermeiden, kann man mittels `try: .. except...` diesen Fehler abfangen 

In [ ]:
import yfinance as yf

alz = yf.Ticker("ALV.DE")

#### Erstelle einen Dataframe, der die Kursdaten der letzten 12 Monate enthält
df2 = alz.history(period="1y", interval = "1d")


print(df2.tail(5))
# Gibt die letzten fünf Zeilen der Kursdaten aus – ideal zur Kontrolle.

In [ ]:
#speichern der Daten in CSV-Datei
df2.to_csv('alz_12months.csv')

Der folgende Code verursacht keinen Skript-Abbruch, falls mal der Yahoo-Download nicht funktioniert.

In [ ]:
import yfinance as yf
import pandas as pd
import pandas_datareader as web   #siehe https://pandas-datareader.readthedocs.io/en/latest/#
from datetime import datetime

ticker = ["TSLA"]

#prices = yf.Ticker(ticker).history('5y')  #aktuell Fehlermeldung wegen Problemen bei Yahoo-Finance


print("Versuche Yahoo Finance für %s:\n" % (ticker))
try:
    data = yf.download(ticker, period = "5y", interval = "1d")
except Exception as e:
    print("Fehler bei Yahoo Daten Download: %s \n" % (e))

if not data.empty:
    print("Daten für %s geladen auf Yahoo-Finance" % ticker)
    print(data.head())
    print("Datentyp Rückgabe yfinance: %s:\n" % type(data))
else:
    print("Probleme mit Yahoo-Finance - keine Daten für %s geladen" % (ticker))



Der folgende Code zeigt, wie gleichzeitig Kurse für verschiedene Aktien heruntergeladen werden können:

In [ ]:
tickers = ["AAPL","ALV.DE"]

print("\nVersuche Yahoo Finance für mehrere Assets %s :\n" % (tickers))
all_prices = {}
try:
    data2 = yf.download(tickers, period = "5y", interval = "1d", group_by = "ticker")     
except Exception as e:    
    print("Fehler bei Yahoo Daten Download: %s \n" % (e))

if not data2.empty:                            
    print(data2.head())
    #print(type(data2))
    print("Datentyp Rückgabe yfinance: %s\n"  % (type(data2)))
    print("Infos DataFrame:\n" )
    print(data2.info())


Neben dem Abruf von Kursdaten von Yahoo-Finance besteht ebenfalls die Möglichkeit mittels API-Schnittstellen auf Kursinformationen zuzugreifen. Ein API-Schnittstellen Provider ist [Alpha Vantage](https://www.alphavantage.co/support/#api-key). Nach Registrierung und Erhalt des API-Keys können wir nun auf Börsenkurse zugreifen. Dafür verwenden wir folgenden Code:

In [ ]:
from alpha_vantage.timeseries import TimeSeries
import pandas as pd

#### API-Key für Alpha Vantage angeben
api_key = 'DasistkeinechterAPI-Key'

#### Verbindung zu Alpha Vantage aufbauen
ts = TimeSeries(key=api_key, output_format='pandas')
# Erstellt ein TimeSeries-Objekt ts, über das du dann Methoden wie get_daily verwenden kannst.
# Mit output_format='pandas' bekommst du die Daten direkt als pandas DataFrame. Pandas ist sehr praktisch und einfach von der Handhabung

####  Tagesdaten abrufen
data, meta_data = ts.get_daily(symbol='AAPL', outputsize='compact')
# symbol='AAPL' fragt die Daten für die Apple-Aktie ab.
# data enthält die eigentlichen Kurse (Open, High, Low, Close, Volume), meta_data enthält Zusatzinfos (z. B. Abfragezeitpunkt, Symbol).

print(data.head())
# Gibt die ersten fünf Zeilen der Kursdaten aus.

Werden mehrere Aktien gleichzeitig abgerufen... - Type! 

Mithilfe des Parameters `outputsize` können wir festlegen, wie viele Daten wir anfordern. Mit dem Wert `compact` werden nur die letzten 100 Datenpunkte angefordert. Verwenden wir `full` fordern wir hingegen den gesamten Datenbestand an. 

**1. Hinweis:** In der Regel haben kostenlose API-Schnittstellen die Tücke, nur ein begrenztes Limit an Abfragen pro Minute oder Tag anfordern zu können. Somit kann der Parameterwert `full` demnach dazu führen, dass dieses Limit schneller erreicht ist. Aber auch `yfinance` blockiert in der Regel bei zu vielen Anfragen temporär die IP-Adresse. Zur Lösung dieses Problems können die Schlusskurse als csv-Datei abgespeichert werden, somit stehen sie lokal zur Verfügung. Das kann mithilfe des nachfolgenden Codes durchgeführt werden. Der Code wird hier nur angezeigt, aber nicht ausgeführt, da verhindert werden soll, dass bei jedem Durchlauf dieses Jupyter-Skriptes ein Download erfolgt.

```python
 import yfinance as yf
 import pandas as pd

 Ticker-Symbol für Allianz SE an der Börse Frankfurt/Xetra
 ticker = "ALV.DE"

 #Daten abrufen (01.01.2020 bis 01.01.2025)
 data = yf.download(ticker, start="2020-01-01", end="2025-01-01")

 # Nur Schlusskurse extrahieren
 schlusskurse = data[["Close"]].rename(columns={"Close": "Schlusskurs"})

 # Als CSV-Datei speichern
 schlusskurse.to_csv("Allianz_Schlusskurse_2020_2025.csv")

 print("CSV-Datei wurde gespeichert: Allianz_Schlusskurse_2020_2025.csv")
```

In [ ]:
# import yfinance as yf
# import pandas as pd

# Ticker-Symbol für Allianz SE an der Börse Frankfurt/Xetra
# ticker = "ALV.DE"

# Daten abrufen (01.01.2020 bis 01.01.2025)
# data = yf.download(ticker, start="2020-01-01", end="2025-01-01")

# Nur Schlusskurse extrahieren
# schlusskurse = data[["Close"]].rename(columns={"Close": "Schlusskurs"})

# Als CSV-Datei speichern
# schlusskurse.to_csv("Allianz_Schlusskurse_2020_2025.csv")

# print("CSV-Datei wurde gespeichert: Allianz_Schlusskurse_2020_2025.csv")

**2. Hinweis:** Alpha Vantage liefert in der kostenlosen Version nur Daten für US-Börsen. Dies ist auch der Grund, wieso wir in dem letzten Code Kursdaten von Apple angefordert haben.

mit Pandas Data-Reader: to do -- pip...

In [ ]:
import pandas_datareader.data as web
import datetime

# Zeitraum
start = datetime.datetime(2022, 1, 1)
end = datetime.datetime(2023, 1, 1)

# Apple von Yahoo Finance
#df = web.DataReader("AAPL", "yahoo", start, end)
#print(df.head())

In [ ]:
#stooq

df = web.DataReader("AAPL", "stooq", start, end)
print(df.head())

In [ ]:
# FRED Daten: 3-Monats-T-Bill Rate („TB3MS“):
df = web.DataReader("TB3MS", "fred", start, end)
print(df.tail())

## Darstellung der Kursentwicklung

### Visualisierung mit Matplotlib oder Seaborn

In [ ]:
import yfinance as yf
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime


start_date = datetime(year = 2024, month=1, day = 1)

ticker1 = "AAPL"
stock1 = yf.download(ticker1, start = start_date)
stock1.head()
stock1.tail()

stock1['Close']

plt.figure()
plt.plot(stock1['Close'], label='Closing Price', color='blue')
plt.xlabel("Date")
#plt.xticks(rotation=90)
plt.xticks(rotation=45, ha='right')
plt.legend()
plt.grid()
plt.title(ticker1)
plt.show()


In [ ]:
#multiple stocks
### Multiple Stocks: Achtung group_by hat Einfluss auf die Struktur des "Doppelarrays"

tickers = ["AAPL","NVDA","META"]
stocks_v1 = yf.download(tickers, start_date,   group_by='ticker') #place ticker name as the top-level column
stocks_v2 = yf.download(tickers, start_date,   group_by='column') # place the OHLCV values as the top-level columns

last_date = stocks_v1[tickers[0]]['Close'].index[-1].date() #.strftime("")

Darstellung mittels Seaborn: Aktie für Aktie mittels For-Loop

In [ ]:
plt.figure()
sns.set(style='whitegrid')

for tick in tickers:
    sns.lineplot(data = stocks_v1[tick]["Close"],label=tick)

plt.title("Stock Closing Prices %s -- %s" % (start_date.date(), last_date))
plt.xticks(rotation=45, ha='right')
plt.xlabel("Date")
plt.ylabel("Closing Price ($)")
plt.tight_layout()
plt.show()

Darstellung mehrere Aktienkurse (bei Multi-Abruf `group_by='ticker'`) mittels Seaborn

In [ ]:
plt.figure()
sns.set(style='whitegrid')
sns.relplot(data=stocks_v2['Close'], kind="line",  dashes=False)
plt.title("Stock Closing Prices %s -- %s" % (start_date.date(), last_date))
plt.xticks(rotation=45, ha='right')
plt.xlabel("Date")
plt.ylabel("Closing Price ($)")
plt.tight_layout()

plt.show()


### Visualisierung und technische Chartanalyse von Kursdaten mittels Mplchart

Das Paket `mplchart`, siehe [Webseite](https://pypi.org/project/mplchart/) oder [Github](https://github.com/furechan/mplchart), liefert eine einfache Möglichkeit Charts der technischen Analyse zu erstellen.

<!--
In diesem Abschnitt gehen wir dazu über, unsere Kursdaten zu visualieren. Wir bleiben bei unserer Allianz-Aktie und verwenden das Package `mplchart`, siehe [Webseite](https://pypi.org/project/mplchart/) oder [Github](https://github.com/furechan/mplchart).
-->

In [ ]:
#to do: bitte Demo fuer CSV-Datensatz von oben!! und dann nur zusaetzlich mittels try... fuer aktuelle Daten

from mplchart.chart import Chart
from mplchart.primitives import Candlesticks, Volume
from mplchart.indicators import SMA, RSI, MACD

#Achtung: input mplchart sind OHLCV-DataFrames (also Open, High, Low, Close, Volume mit Datetime-Index, wie yfinance liefert!!!!

# Konfiguration
max_bars = 252 # Zeige das letzte Börsenjahr (in Deutschland gibt es 252 Handelstage) 
indicators = [
    Candlesticks(),
    Volume(),
    SMA(50), 
    SMA(200),
    RSI(), 
    MACD(), 
]

#Daten aus CSV-Datei oben
ticker1 = 'ALV.DE aus CSV'

print(df1["Schlusskurs"].head())  #nicht in OHLCV-Format!!!

#erzeugen kuenstlich dieses Format: Achtung nur Close richtig!!!
ohlc = pd.DataFrame({
    "Date": pd.to_datetime(df1["Datum"]),
    "Open": df1["Schlusskurs"]-10,
    "High": df1["Schlusskurs"] + 20,
    "Low": df1["Schlusskurs"]-20,
    "Close": df1["Schlusskurs"],
    "Volume": 0, #})
}, index=df1.index)

#ohlc["Date"] = pd.to_datetime(ohlc["Date"])
ohlc = ohlc.set_index("Date")

print("Umgewandelter DataFrame:\n")
print(ohlc.head())
print(ohlc.info())






In [ ]:
# Plot erzeugen -- to do line 40
chart1 = Chart(ticker1, max_bars=max_bars)
chart1.plot(ohlc, indicators)  #to do: Achtung hier macht Candlestick keinen Sinn, da nur Closing Prices!!
chart1.show()

In [ ]:
from mplchart.chart import Chart
from mplchart.primitives import Candlesticks, Volume
from mplchart.indicators import SMA, RSI, MACD

#Achtung: input mplchart sind OHLCV-DataFrames (also Open, High, Low, Close, Volume mit Datetime-Index, wie yfinance liefert!!!!

# Konfiguration
max_bars = 252 #Beschränkung auf das letzte Börsenjahr (in Deutschland gibt es 252 Handelstage) 
indicators = [
    Candlesticks(),
    Volume(),
    SMA(50), 
    SMA(200),
    RSI(), 
    MACD(), 
]


# Daten von Yahoo-Finance abrufen
ticker = "ALV.DE"

print("Versuche Yahoo Finance für %s:\n" % (ticker))
try:
    data = yf.Ticker(ticker).history('2y')  #hier ggf. Zeiten anpassen
except Exception as e:
    print("Fehler bei Yahoo Daten Download: %s \n" % (e))

if not data.empty:
    print(data.head())
    chart = Chart(title = ticker, max_bars=max_bars)
    chart.plot(data, indicators)
    chart.show()
   

>❓ **Frage:** Wir können wir diesen Chart nun interpretieren? 

Der _Relative Strenght Index_ ist ein sogenannter Momentum-Indikator, der in der technischen Analyse verwendet wird und das Ausmaß der jüngsten Kursveränderungen misst. Ein RSI-Wert von 70 oder mehr deutet darauf hin, dass ein Wertpapier überkauft oder überbewertet ist und möglicherweise für eine Trendumkehr oder einen korrigierenden Kursrückgang bereit ist. Ein RSI-Wert von 30 oder darunter weist auf einen überverkauften oder unterbewerteten Zustand hin. Dabei dient zur Berechnung üblicherweise ein Zeitraum über 14 Tage, mitunter auch über acht oder 38 Tage. 

Der _Moving Average Convergence/Divergence_ ist ein Indikator für Trendwechsel. Kreuzt die schwarze Linie über die blaue Linie, entsteht ein Kaufsignal. Kreuzt die blaue Linie über die schwarze Linie, entsteht ein Verkaufssignal.

Der _Simple Moving Average_ ist das artithmetische Mittel der letzten t-Handelstage (in unserem Fall der letzten 50 und 200 Handelstage). Ein steigender SMA deutet auf einen Aufwärtstrend hin, während ein fallender SMA auf einen Abwärtstrend schließen lässt (Trendbestimmungsfunktion). Wenn der Kurs von unten an den SMA stößt und von dort abprallt, kann dies als Kaufsignal interpretiert werden. Umgekehrt kann ein Stoß von oben und ein Abprallen nach unten als Verkaufssignal gelten. (Funktion als Wiederstands- und Unterstützungszone).
 
>👉 Weitere Informationen zu Indikatoren finden Sie auf folgender [Webseite](https://www.boerse.de/technische-indikatoren/). 

>💡 **Aufgabe:** Versuchen Sie im Selbststudium weitere Chartindiaktoren zu verwenden und interpretieren.